In [9]:
!nvidia-smi

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Mon Jul 29 12:22:16 2024       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.90.07              Driver Version: 550.90.07      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla P100-PCIE-16GB           Off |   00000000:00:04.0 Off |                    0 |
| N/A   39C    P0             31W /  250W |    1913MiB /  16384MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [10]:
import torch


# Function to list available GPUs and select one
def select_device():
    if torch.cuda.is_available():
        print("Available GPUs:")
        for i in range(torch.cuda.device_count()):
            print(f"{i}: {torch.cuda.get_device_name(i)}")
        device_id = int(input("Select GPU by entering the device ID (default 0): ") or 0)
        if device_id < torch.cuda.device_count():
            print(f"Using GPU: {torch.cuda.get_device_name(device_id)}")
            return torch.device(f"cuda:{device_id}")
        else:
            print(f"Invalid device ID. Using GPU: {torch.cuda.get_device_name(0)}")
            return torch.device("cuda:0")
    else:
        print("No GPU available. Using CPU.")
        return torch.device("cpu")

# Select the device
device = select_device()

Available GPUs:
0: Tesla P100-PCIE-16GB


Select GPU by entering the device ID (default 0):  0


Using GPU: Tesla P100-PCIE-16GB


In [11]:
# Import Libraries and Load Model/Tokenizer
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import pandas as pd
import torch
from tqdm.auto import tqdm

model_name = "microsoft/deberta-large-mnli"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSequenceClassification.from_pretrained(model_name)

device = "cuda" if torch.cuda.is_available() else "cpu"
model.to(device)

Some weights of the model checkpoint at microsoft/deberta-large-mnli were not used when initializing DebertaForSequenceClassification: ['config']
- This IS expected if you are initializing DebertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DebertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


DebertaForSequenceClassification(
  (deberta): DebertaModel(
    (embeddings): DebertaEmbeddings(
      (word_embeddings): Embedding(50265, 1024, padding_idx=0)
      (LayerNorm): DebertaLayerNorm()
      (dropout): StableDropout()
    )
    (encoder): DebertaEncoder(
      (layer): ModuleList(
        (0-23): 24 x DebertaLayer(
          (attention): DebertaAttention(
            (self): DisentangledSelfAttention(
              (in_proj): Linear(in_features=1024, out_features=3072, bias=False)
              (pos_dropout): StableDropout()
              (pos_proj): Linear(in_features=1024, out_features=1024, bias=False)
              (pos_q_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (dropout): StableDropout()
            )
            (output): DebertaSelfOutput(
              (dense): Linear(in_features=1024, out_features=1024, bias=True)
              (LayerNorm): DebertaLayerNorm()
              (dropout): StableDropout()
            )
          )
   

In [12]:
# SNLI test dataset

df_snli = pd.read_csv('/kaggle/input/stanford-natural-language-inference-corpus/snli_1.0_test.csv')

In [13]:
df_snli

gold_label                             sentence1_binary_parse  \
0           neutral  ( ( This ( church choir ) ) ( ( ( sings ( to (...   
1        entailment  ( ( This ( church choir ) ) ( ( ( sings ( to (...   
2     contradiction  ( ( This ( church choir ) ) ( ( ( sings ( to (...   
3           neutral  ( ( ( A woman ) ( with ( ( ( ( ( a ( green hea...   
4        entailment  ( ( ( A woman ) ( with ( ( ( ( ( a ( green hea...   
...             ...                                                ...   
9995  contradiction  ( ( Two women ) ( ( are ( ( observing somethin...   
9996     entailment  ( ( Two women ) ( ( are ( ( observing somethin...   
9997  contradiction  ( ( ( ( ( A man ) ( in ( a ( black ( leather j...   
9998     entailment  ( ( ( ( ( A man ) ( in ( a ( black ( leather j...   
9999        neutral  ( ( ( ( ( A man ) ( in ( a ( black ( leather j...   

                                 sentence2_binary_parse  \
0     ( ( The church ) ( ( has ( cracks ( in ( the c...   
1     ( ( The church ) ( ( is ( filled ( with song )...   
2     ( ( ( A choir ) ( singing ( at ( a ( baseball ...   
3                  ( ( The woman ) ( ( is young ) . ) )   
4         ( ( The woman ) ( ( is ( very happy ) ) . ) )   
...                                                 ...   
9995  ( ( ( Two women ) ( are ( standing ( with ( th...   
9996  ( ( Two girls ) ( ( are ( looking ( at somethi...   
9997   ( ( A man ) ( ( is ( flying ( a kite ) ) ) . ) )   
9998  ( ( A man ) ( ( is ( speaking ( in ( a classro...   
9999  ( ( A man ) ( ( is ( ( teaching science ) ( in...   

                                        sentence1_parse  \
0     (ROOT (S (NP (DT This) (NN church) (NN choir))...   
1     (ROOT (S (NP (DT This) (NN church) (NN choir))...   
2     (ROOT (S (NP (DT This) (NN church) (NN choir))...   
3     (ROOT (NP (NP (DT A) (NN woman)) (PP (IN with)...   
4     (ROOT (NP (NP (DT A) (NN woman)) (PP (IN with)...   
...                                                 ...   
9995  (ROOT (S (NP (CD Two) (NNS women)) (VP (VBP ar...   
9996  (ROOT (S (NP (CD Two) (NNS women)) (VP (VBP ar...   
9997  (ROOT (S (NP (NP (NP (DT A) (NN man)) (PP (IN ...   
9998  (ROOT (S (NP (NP (NP (DT A) (NN man)) (PP (IN ...   
9999  (ROOT (S (NP (NP (NP (DT A) (NN man)) (PP (IN ...   

                                        sentence2_parse  \
0     (ROOT (S (NP (DT The) (NN church)) (VP (VBZ ha...   
1     (ROOT (S (NP (DT The) (NN church)) (VP (VBZ is...   
2     (ROOT (NP (NP (DT A) (NN choir)) (VP (VBG sing...   
3     (ROOT (S (NP (DT The) (NN woman)) (VP (VBZ is)...   
4     (ROOT (S (NP (DT The) (NN woman)) (VP (VBZ is)...   
...                                                 ...   
9995  (ROOT (S (NP (NP (CD Two) (NNS women)) (SBAR (...   
9996  (ROOT (S (NP (CD Two) (NNS girls)) (VP (VBP ar...   
9997  (ROOT (S (NP (DT A) (NN man)) (VP (VBZ is) (VP...   
9998  (ROOT (S (NP (DT A) (NN man)) (VP (VBZ is) (VP...   
9999  (ROOT (S (NP (DT A) (NN man)) (VP (VBZ is) (VP...   

                                              sentence1  \
0     This church choir sings to the masses as they ...   
1     This church choir sings to the masses as they ...   
2     This church choir sings to the masses as they ...   
3     A woman with a green headscarf, blue shirt and...   
4     A woman with a green headscarf, blue shirt and...   
...                                                 ...   
9995        Two women are observing something together.   
9996        Two women are observing something together.   
9997  A man in a black leather jacket and a book in ...   
9998  A man in a black leather jacket and a book in ...   
9999  A man in a black leather jacket and a book in ...   

                                           sentence2         captionID  \
0              The church has cracks in the ceiling.  2677109430.jpg#1   
1                    The church is filled with song.  2677109430.jpg#1   
2                A choir singing at a baseball game.  26771094

In [14]:
!pip install shap transformers


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [17]:
from transformers import pipeline
import shap

# Select the first sample
sample = df_snli.iloc[0]

# Prepare premises and hypotheses
premise = sample['sentence1']
hypothesis = sample['sentence2']
true_label = sample['gold_label']

# Tokenize the sample
tokenized = tokenizer(premise, hypothesis, truncation=True, padding=True, return_tensors="pt").to(device)

# Define a prediction function
def predict(inputs):
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.logits.cpu().numpy()

# Make a prediction
logits = predict(tokenized)
prediction = logits.argmax(axis=1).item()
label_map = {0: "entailment", 1: "neutral", 2: "contradiction"}

print("Sample 1")
print(f"Premise: {premise}")
print(f"Hypothesis: {hypothesis}")
print(f"True Label: {true_label}")

# Create a SHAP explainer using the transformers pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0, return_all_scores=True)

# Create a SHAP explainer for transformers
explainer = shap.Explainer(pipe)

# Prepare the combined text input for SHAP
combined_input = [f"{premise}. {hypothesis}"]

# Calculate SHAP values for the combined input
shap_values = explainer(combined_input)

# Visualize the explanations for the first sample
shap.plots.text(shap_values[0])

Sample 1
Premise: This church choir sings to the masses as they sing joyous songs from the book at a church.
Hypothesis: The church has cracks in the ceiling.
True Label: neutral


`return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:25, 25.00s/it]               


In [18]:

# Select the first sample
sample = df_snli.iloc[1]

# Prepare premises and hypotheses
premise = sample['sentence1']
hypothesis = sample['sentence2']
true_label = sample['gold_label']

# Tokenize the sample
tokenized = tokenizer(premise, hypothesis, truncation=True, padding=True, return_tensors="pt").to(device)

# Define a prediction function
def predict(inputs):
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.logits.cpu().numpy()

# Make a prediction
logits = predict(tokenized)
prediction = logits.argmax(axis=1).item()
label_map = {0: "entailment", 1: "neutral", 2: "contradiction"}

print("Sample 2")
print(f"Premise: {premise}")
print(f"Hypothesis: {hypothesis}")
print(f"True Label: {true_label}")

# Create a SHAP explainer using the transformers pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0, return_all_scores=True)

# Create a SHAP explainer for transformers
explainer = shap.Explainer(pipe)

# Prepare the combined text input for SHAP
combined_input = [f"{premise}. {hypothesis}"]

# Calculate SHAP values for the combined input
shap_values = explainer(combined_input)

# Visualize the explanations for the first sample
shap.plots.text(shap_values[0])

`return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.


Sample 2
Premise: This church choir sings to the masses as they sing joyous songs from the book at a church.
Hypothesis: The church is filled with song.
True Label: entailment


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:21, 21.70s/it]               


In [19]:

# Select the first sample
sample = df_snli.iloc[2]

# Prepare premises and hypotheses
premise = sample['sentence1']
hypothesis = sample['sentence2']
true_label = sample['gold_label']

# Tokenize the sample
tokenized = tokenizer(premise, hypothesis, truncation=True, padding=True, return_tensors="pt").to(device)

# Define a prediction function
def predict(inputs):
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.logits.cpu().numpy()

# Make a prediction
logits = predict(tokenized)
prediction = logits.argmax(axis=1).item()
label_map = {0: "entailment", 1: "neutral", 2: "contradiction"}

print("Sample 3")
print(f"Premise: {premise}")
print(f"Hypothesis: {hypothesis}")
print(f"True Label: {true_label}")

# Create a SHAP explainer using the transformers pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0, return_all_scores=True)

# Create a SHAP explainer for transformers
explainer = shap.Explainer(pipe)

# Prepare the combined text input for SHAP
combined_input = [f"{premise}. {hypothesis}"]

# Calculate SHAP values for the combined input
shap_values = explainer(combined_input)

# Visualize the explanations for the first sample
shap.plots.text(shap_values[0])

Sample 3
Premise: This church choir sings to the masses as they sing joyous songs from the book at a church.
Hypothesis: A choir singing at a baseball game.
True Label: contradiction


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:21, 21.36s/it]               


In [20]:

# Select the first sample
sample = df_snli.iloc[4]

# Prepare premises and hypotheses
premise = sample['sentence1']
hypothesis = sample['sentence2']
true_label = sample['gold_label']

# Tokenize the sample
tokenized = tokenizer(premise, hypothesis, truncation=True, padding=True, return_tensors="pt").to(device)

# Define a prediction function
def predict(inputs):
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.logits.cpu().numpy()

# Make a prediction
logits = predict(tokenized)
prediction = logits.argmax(axis=1).item()
label_map = {0: "entailment", 1: "neutral", 2: "contradiction"}

print("Sample 4")
print(f"Premise: {premise}")
print(f"Hypothesis: {hypothesis}")
print(f"True Label: {true_label}")

# Create a SHAP explainer using the transformers pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0, return_all_scores=True)

# Create a SHAP explainer for transformers
explainer = shap.Explainer(pipe)

# Prepare the combined text input for SHAP
combined_input = [f"{premise}. {hypothesis}"]

# Calculate SHAP values for the combined input
shap_values = explainer(combined_input)

# Visualize the explanations for the first sample
shap.plots.text(shap_values[0])

Sample 4
Premise: A woman with a green headscarf, blue shirt and a very big grin.
Hypothesis: The woman is very happy.
True Label: entailment


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:21, 21.21s/it]               


In [21]:

# Select the first sample
sample = df_snli.iloc[6]

# Prepare premises and hypotheses
premise = sample['sentence1']
hypothesis = sample['sentence2']
true_label = sample['gold_label']

# Tokenize the sample
tokenized = tokenizer(premise, hypothesis, truncation=True, padding=True, return_tensors="pt").to(device)

# Define a prediction function
def predict(inputs):
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.logits.cpu().numpy()

# Make a prediction
logits = predict(tokenized)
prediction = logits.argmax(axis=1).item()
label_map = {0: "entailment", 1: "neutral", 2: "contradiction"}

print("Sample 5")
print(f"Premise: {premise}")
print(f"Hypothesis: {hypothesis}")
print(f"True Label: {true_label}")

# Create a SHAP explainer using the transformers pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0, return_all_scores=True)

# Create a SHAP explainer for transformers
explainer = shap.Explainer(pipe)

# Prepare the combined text input for SHAP
combined_input = [f"{premise}. {hypothesis}"]

# Calculate SHAP values for the combined input
shap_values = explainer(combined_input)

# Visualize the explanations for the first sample
shap.plots.text(shap_values[0])

Sample 5
Premise: An old man with a package poses in front of an advertisement.
Hypothesis: A man poses in front of an ad.
True Label: entailment


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:21, 21.45s/it]               


In [22]:

# Select the first sample
sample = df_snli.iloc[10]

# Prepare premises and hypotheses
premise = sample['sentence1']
hypothesis = sample['sentence2']
true_label = sample['gold_label']

# Tokenize the sample
tokenized = tokenizer(premise, hypothesis, truncation=True, padding=True, return_tensors="pt").to(device)

# Define a prediction function
def predict(inputs):
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.logits.cpu().numpy()

# Make a prediction
logits = predict(tokenized)
prediction = logits.argmax(axis=1).item()
label_map = {0: "entailment", 1: "neutral", 2: "contradiction"}

print("Sample 6")
print(f"Premise: {premise}")
print(f"Hypothesis: {hypothesis}")
print(f"True Label: {true_label}")

# Create a SHAP explainer using the transformers pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0, return_all_scores=True)

# Create a SHAP explainer for transformers
explainer = shap.Explainer(pipe)

# Prepare the combined text input for SHAP
combined_input = [f"{premise}. {hypothesis}"]

# Calculate SHAP values for the combined input
shap_values = explainer(combined_input)

# Visualize the explanations for the first sample
shap.plots.text(shap_values[0])

Sample 6
Premise: A statue at a museum that no seems to be looking at.
Hypothesis: There is a statue that not many people seem to be interested in.
True Label: entailment


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:21, 21.48s/it]               


In [23]:

# Select the first sample
sample = df_snli.iloc[11]

# Prepare premises and hypotheses
premise = sample['sentence1']
hypothesis = sample['sentence2']
true_label = sample['gold_label']

# Tokenize the sample
tokenized = tokenizer(premise, hypothesis, truncation=True, padding=True, return_tensors="pt").to(device)

# Define a prediction function
def predict(inputs):
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.logits.cpu().numpy()

# Make a prediction
logits = predict(tokenized)
prediction = logits.argmax(axis=1).item()
label_map = {0: "entailment", 1: "neutral", 2: "contradiction"}

print("Sample 7")
print(f"Premise: {premise}")
print(f"Hypothesis: {hypothesis}")
print(f"True Label: {true_label}")

# Create a SHAP explainer using the transformers pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0, return_all_scores=True)

# Create a SHAP explainer for transformers
explainer = shap.Explainer(pipe)

# Prepare the combined text input for SHAP
combined_input = [f"{premise}. {hypothesis}"]

# Calculate SHAP values for the combined input
shap_values = explainer(combined_input)

# Visualize the explanations for the first sample
shap.plots.text(shap_values[0])

Sample 7
Premise: A statue at a museum that no seems to be looking at.
Hypothesis: Tons of people are gathered around the statue.
True Label: contradiction


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:21, 21.37s/it]               
